In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F 
import torch.autograd
from torch.autograd import Variable
import torch.optim as optim
import numpy as np
import gym
from collections import deque
import random
import sys
import pandas as pd
import matplotlib.pyplot as plt
from numpy import cos, sin
from gym import spaces
from gym.error import DependencyNotInstalled
from typing import Optional
from control.matlab import ss, lsim, linspace, c2d
from functools import partial
from state_estimation import Estimator
import math
import gym
from stable_baselines3 import PPO, SAC, TD3, DDPG, DQN, A2C
from stable_baselines3.common.env_checker import check_env
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import odeint

In [ ]:
import os
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"

In [ ]:
# define CSTR model
def bicycle(x,t,u, params={}):
    lr = 1.105
    lf = 1.738
    psi = x[2]
    v = x[3]
    alpha = u[0]
    sigma = u[1]
    xdot =np.zeros(4)
    beta = math.atan((lr/(lr+lf)*math.tan(sigma)))
    xdot[0] = v*math.cos(psi+beta)
    xdot[1] = v*math.sin(psi+beta)
    xdot[2] = v/lr*math.sin(beta)
    xdot[3] = alpha
    return xdot

In [ ]:
class bicycleEnv(gym.Env):
    """Custom Environment that follows gym interface."""

    metadata = {"render.modes": ["human"]}

    def __init__(self, render_mode: Optional[str] = None, g=10.0):
        super(bicycleEnv).__init__()
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:
        ob_high = np.ones(4)*20
        action_high = np.ones(2)*7
        self.action_space = spaces.Box(low=-action_high, high=action_high, dtype=np.float32)
        self.observation_space = spaces.Box(low=-ob_high, high=ob_high, dtype=np.float32)
        self.step_const = 20
        self.freq = 0.1
        self.steps = 0
        self.center = [1,1,0,math.sqrt(2)]
        self.obstacle = [0.5,0.5,0,math.sqrt(2)/2]
        self.reward_cache = [] # cache distances to target norm ball center
        self.final_reward_cache = [] # cache final reward
        self.state = np.random.rand(4)*2-1
        self.horizon = np.arange(0, self.step_const+2, 1)*0.1
        self.target_norm_radius = 0.8
        self.safe_norm_radius = 0.4
        self.max_reward_list = []
        self.avoid_reward_cache = [] 
        self.quality_list = []
        self.total_steps = 0
        self.step_history = []
        self.k = 20
    def step(self, action):
        terminated = False
        ts = [self.horizon[self.steps], self.horizon[self.steps+1] ]
        self.state = odeint(bicycle, self.state, ts, args=(action,))[-1]
        dist = np.linalg.norm(self.state - self.center)
        obs_dist = np.linalg.norm(self.state - self.obstacle)
        reward = self.target_norm_radius - dist
        obs_reward = obs_dist - self.safe_norm_radius
        # reward = self.target_norm_radius - dist + obs_dist - 0.3
        self.reward_cache.append(reward)
        self.avoid_reward_cache.append(obs_reward)
        if self.steps < 10:
            reach_reward = max(self.reward_cache)
        else:
            reach_reward = max(self.reward_cache[-10:])
        if self.steps < 10:
            avoid_reward = min(self.avoid_reward_cache)
        else:
            avoid_reward = min(self.avoid_reward_cache[-10:])    
        final_reward = min(reach_reward, avoid_reward)
        self.reward_cache.append(reward)
        self.steps += 1
        self.total_steps +=1
        # quantitative semantics
        # reach reward, encourage reaching target
        # if self.steps < 10:
        #     reach_reward = max(self.reward_cache)
        # else:
        #     reach_reward = max(self.reward_cache[-10:])
        # final_reward = reach_reward
        if dist <= self.target_norm_radius:
            final_reward = 10
        self.final_reward_cache.append(final_reward)
        if self.steps == self.step_const or max(np.absolute(self.state))>20 or obs_dist<=self.safe_norm_radius:
            self.max_reward_list.append(max(self.final_reward_cache)) # use max final reward to measure episodes
            self.step_history.append(self.total_steps)
            self.quality_list.append(sum(self.final_reward_cache))
            terminated = True
            self.reset()

        # Return next state, reward, done, info
        return self.state, final_reward, terminated, {}

    def reset(self):
        self.steps = 0
        # self.state = np.random.rand(4)*2-1
        self.state = np.random.rand(4)*2-1.2
        self.reward_cache = []
        self.step_const = self.k
        self.horizon = np.arange(0, self.step_const+2, 1)*0.1
        self.final_reward_cache = []
        return self.state  # reward, done, info can't be included

    def render(self, mode="human"):
        return

    def close(self):
        if self.screen is not None:
            import pygame
            pygame.display.quit()
            pygame.quit()
            self.isopen = False

In [ ]:
# Training
reached = []
for k in [20]:
    env = bicycleEnv()
    env.k = k
    print('Start training with PPO ...')
    # learning_rate = 1e-3, n_steps = 1024, tune these
    model = SAC("MlpPolicy", env, verbose=0)
    model.learn(total_timesteps=300000, progress_bar=False)
    vec_env = model.get_env()
    obs = vec_env.reset()
    env = bicycleEnv()
    env.k = 160
    state = env.reset()
    dims0 = []
    dims1 = []
    dims2 = []
    dims3 = []
    euclids = []
    center = [1,1,0,math.sqrt(2)]
    obstacle = [0.5,0.5,0,math.sqrt(2)/2]
    num_reached = 0
    for j in range(1000):
        dim0 = []
        dim1 = []
        dim2 = []
        dim3 = []
        euclid = []
        state = env.reset()
        # Print initial state
        for i in range(30):
            action, _states = model.predict(state, deterministic=True)
            new_state, reward, done, _ = env.step(action)
            dim0.append(state[0])
            dim1.append(state[1])
            dim2.append(state[2])
            dim3.append(state[3])
            dist = np.linalg.norm(new_state-center)
            obs_dist = np.linalg.norm(new_state-obstacle)
            euclid.append(dist)
            state = new_state
            if obs_dist <= env.safe_norm_radius:
                break
            if dist <= env.target_norm_radius: # stop
                num_reached += 1
                break
        dims0.append(dim0)
        dims1.append(dim1)
        dims2.append(dim2)
        dims3.append(dim3)
        euclids.append(euclid)
    reached.append(num_reached)

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 5.45     |
| time/              |          |
|    episodes        | 1084     |
|    fps             | 62       |
|    time_elapsed    | 345      |
|    total_timesteps | 21524    |
| train/             |          |
|    actor_loss      | -5.26    |
|    critic_loss     | 42.6     |
|    ent_coef        | 0.0702   |
|    ent_coef_loss   | 0.418    |
|    learning_rate   | 0.0003   |
|    n_updates       | 21423    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 4.19     |
| time/              |          |
|    episodes        | 1088     |
|    fps             | 62       |
|    time_elapsed    | 346      |
|    total_timesteps | 21604    |
| train/             |          |
|    actor_loss      | -9.5     |
|    critic_loss     | 36.9     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 3.28     |
| time/              |          |
|    episodes        | 1144     |
|    fps             | 62       |
|    time_elapsed    | 366      |
|    total_timesteps | 22724    |
| train/             |          |
|    actor_loss      | -6.81    |
|    critic_loss     | 30.3     |
|    ent_coef        | 0.0695   |
|    ent_coef_loss   | 1.08     |
|    learning_rate   | 0.0003   |
|    n_updates       | 22623    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 4.48     |
| time/              |          |
|    episodes        | 1148     |
|    fps             | 62       |
|    time_elapsed    | 367      |
|    total_timesteps | 22804    |
| train/             |          |
|    actor_loss      | -8.58    |
|    critic_loss     | 35.4     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 9.96     |
| time/              |          |
|    episodes        | 1204     |
|    fps             | 61       |
|    time_elapsed    | 385      |
|    total_timesteps | 23924    |
| train/             |          |
|    actor_loss      | -11.3    |
|    critic_loss     | 65.4     |
|    ent_coef        | 0.0679   |
|    ent_coef_loss   | 0.064    |
|    learning_rate   | 0.0003   |
|    n_updates       | 23823    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 12       |
| time/              |          |
|    episodes        | 1208     |
|    fps             | 61       |
|    time_elapsed    | 387      |
|    total_timesteps | 24004    |
| train/             |          |
|    actor_loss      | -10.4    |
|    critic_loss     | 40.7     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 6.85     |
| time/              |          |
|    episodes        | 1264     |
|    fps             | 61       |
|    time_elapsed    | 405      |
|    total_timesteps | 25124    |
| train/             |          |
|    actor_loss      | -7.37    |
|    critic_loss     | 33.5     |
|    ent_coef        | 0.0677   |
|    ent_coef_loss   | 0.127    |
|    learning_rate   | 0.0003   |
|    n_updates       | 25023    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 8.5      |
| time/              |          |
|    episodes        | 1268     |
|    fps             | 61       |
|    time_elapsed    | 406      |
|    total_timesteps | 25204    |
| train/             |          |
|    actor_loss      | -9.42    |
|    critic_loss     | 57.6     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 15       |
| time/              |          |
|    episodes        | 1324     |
|    fps             | 61       |
|    time_elapsed    | 424      |
|    total_timesteps | 26324    |
| train/             |          |
|    actor_loss      | -12.9    |
|    critic_loss     | 44.6     |
|    ent_coef        | 0.069    |
|    ent_coef_loss   | 0.675    |
|    learning_rate   | 0.0003   |
|    n_updates       | 26223    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 20       |
|    ep_rew_mean     | 17.1     |
| time/              |          |
|    episodes        | 1328     |
|    fps             | 61       |
|    time_elapsed    | 425      |
|    total_timesteps | 26404    |
| train/             |          |
|    actor_loss      | -8.09    |
|    critic_loss     | 48.9     |
|    ent_coef 

...

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 156      |
|    ep_rew_mean     | 795      |
| time/              |          |
|    episodes        | 1640     |
|    fps             | 72       |
|    time_elapsed    | 3562     |
|    total_timesteps | 258305   |
| train/             |          |
|    actor_loss      | -141     |
|    critic_loss     | 251      |
|    ent_coef        | 0.489    |
|    ent_coef_loss   | 0.0707   |
|    learning_rate   | 0.0003   |
|    n_updates       | 258204   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 156      |
|    ep_rew_mean     | 792      |
| time/              |          |
|    episodes        | 1644     |
|    fps             | 72       |
|    time_elapsed    | 3571     |
|    total_timesteps | 258945   |
| train/             |          |
|    actor_loss      | -150     |
|    critic_loss     | 23.8     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 154      |
|    ep_rew_mean     | 804      |
| time/              |          |
|    episodes        | 1700     |
|    fps             | 72       |
|    time_elapsed    | 3690     |
|    total_timesteps | 267522   |
| train/             |          |
|    actor_loss      | -154     |
|    critic_loss     | 30.8     |
|    ent_coef        | 0.497    |
|    ent_coef_loss   | -0.057   |
|    learning_rate   | 0.0003   |
|    n_updates       | 267421   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 154      |
|    ep_rew_mean     | 787      |
| time/              |          |
|    episodes        | 1704     |
|    fps             | 72       |
|    time_elapsed    | 3699     |
|    total_timesteps | 268162   |
| train/             |          |
|    actor_loss      | -148     |
|    critic_loss     | 203      |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 155      |
|    ep_rew_mean     | 819      |
| time/              |          |
|    episodes        | 1760     |
|    fps             | 72       |
|    time_elapsed    | 3824     |
|    total_timesteps | 276970   |
| train/             |          |
|    actor_loss      | -144     |
|    critic_loss     | 44.4     |
|    ent_coef        | 0.522    |
|    ent_coef_loss   | -0.0351  |
|    learning_rate   | 0.0003   |
|    n_updates       | 276869   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 155      |
|    ep_rew_mean     | 824      |
| time/              |          |
|    episodes        | 1764     |
|    fps             | 72       |
|    time_elapsed    | 3833     |
|    total_timesteps | 277610   |
| train/             |          |
|    actor_loss      | -148     |
|    critic_loss     | 203      |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 159      |
|    ep_rew_mean     | 847      |
| time/              |          |
|    episodes        | 1820     |
|    fps             | 72       |
|    time_elapsed    | 3961     |
|    total_timesteps | 286551   |
| train/             |          |
|    actor_loss      | -160     |
|    critic_loss     | 611      |
|    ent_coef        | 0.507    |
|    ent_coef_loss   | -0.103   |
|    learning_rate   | 0.0003   |
|    n_updates       | 286450   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 159      |
|    ep_rew_mean     | 855      |
| time/              |          |
|    episodes        | 1824     |
|    fps             | 72       |
|    time_elapsed    | 3970     |
|    total_timesteps | 287191   |
| train/             |          |
|    actor_loss      | -161     |
|    critic_loss     | 203      |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 158      |
|    ep_rew_mean     | 835      |
| time/              |          |
|    episodes        | 1880     |
|    fps             | 72       |
|    time_elapsed    | 4094     |
|    total_timesteps | 295931   |
| train/             |          |
|    actor_loss      | -154     |
|    critic_loss     | 692      |
|    ent_coef        | 0.528    |
|    ent_coef_loss   | -0.215   |
|    learning_rate   | 0.0003   |
|    n_updates       | 295830   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 158      |
|    ep_rew_mean     | 823      |
| time/              |          |
|    episodes        | 1884     |
|    fps             | 72       |
|    time_elapsed    | 4103     |
|    total_timesteps | 296571   |
| train/             |          |
|    actor_loss      | -162     |
|    critic_loss     | 19       |
|    ent_coef 

In [ ]:
print(reached)
model.save("SAC_bicycle")

In [ ]:
import cvxpy as cp
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import minimize, Bounds, LinearConstraint, NonlinearConstraint, root
def fgsm_attack(state, model, epsilon, policy, norm, args):
    state = torch.from_numpy(state)
    state = state.detach().unsqueeze(0).requires_grad_(True)
    action = model.actor(state)
    # target = torch.argmax(q_vals).unsqueeze(0)
    # preds = torch.softmax(q_vals, 1)
    # The loss is calcualted with cross entropy
    # current_q = self.critic(state, action)
    # cri = model.critic(state)
    q_vals = (model.critic(state, action))
    loss = (q_vals[0] + q_vals[1]) / 2 * (-1)
    # print(target)
    # loss_func = torch.nn.CrossEntropyLoss()
    # loss = loss_func(preds, target)
    model.actor.zero_grad()
    
    loss.backward()
   
    state_grad = state.grad.detach().squeeze()
    
    state = state.squeeze()
    # Perturb only agent position and ball position
    if norm == float('inf'):
        perturbed_state = state + epsilon * state_grad.sign()
    elif norm == 2:
        perturbed_state = state + epsilon * state_grad / torch.norm(state_grad, norm)
    elif norm == 1:
        index = torch.argmax(state_grad)
        per = torch.zeros_like(state_grad)
        per[index] = 1
        perturbed_state = state + epsilon * per
    return perturbed_state.detach().cpu().numpy()

def safe_attack(env, state, model, epsilon, policy, norm, args):
    action = model.predict(state, deterministic=True)[0]
    # print(action)
    effect = None
    attack = None
    _action = action
    _state = state
    
    def f(x):
    # Objective function
        return 1
    def fun(x):
        return np.linalg.norm(odeint(bicycle, state, ts, args=(x,))[-1] - env.obstacle) >\
                            np.linalg.norm(odeint(bicycle, state, ts, args=(action,))[-1] - env.obstacle)
    x_start = np.array(action)
    lim = [-7, 7]

    bounds = Bounds([lim[0], lim[0]], [lim[1], lim[1]])  

    ts = [env.horizon[env.steps], env.horizon[env.steps+1] ]
    x_state = odeint(bicycle, state, ts, args=(action,))[-1]
    non_linear_eq= lambda x: np.linalg.norm(odeint(bicycle, state, ts, args=(x,))[-1] - env.obstacle) -\
                            np.linalg.norm(odeint(bicycle, state, ts, args=(action,))[-1] - env.obstacle)
    non_linear_constr = NonlinearConstraint(non_linear_eq, 0.0, np.inf)
    result = minimize(f, x_start, method='trust-constr', bounds=bounds, constraints=non_linear_constr)
    # print(result.x)
    op_action = (result.x)
    state = torch.from_numpy(state)
    
    state = state.detach().unsqueeze(0).requires_grad_(True)
    # print(model.predict(state, deterministic=True)[0])
    next_origin_obs_dist =  np.linalg.norm(odeint(bicycle, _state, ts, args=(_action,))[-1] - env.obstacle)
    effect = next_origin_obs_dist
    for i in range(100):
     
        action = model.actor(state, deterministic=True)[0].requires_grad_(True)
        action = action * 7
        action = action.double()
        mse = nn.MSELoss()
        
        # compute the distance
        pdist = torch.nn.PairwiseDistance(p=2)
        loss = pdist(torch.tensor([op_action]), action)
        
        # loss = mse(torch.tensor([op_action]).requires_grad_(True), action)
        model.actor.zero_grad()
        loss = loss.double()
        # print(action.dtype)
        loss.backward()
       
        state_grad = state.grad.detach().squeeze()
        perturbed_state = state - epsilon / 10 * state_grad.sign()
        # print(state_grad)
        # project!
        # print(perturbed_state[0])
        # torch.clamp(perturbed_state, min=(state - epsilon), max=(state + epsilon))
        # print(perturbed_state[0])
        
        scaled_action = model.actor(perturbed_state, deterministic=True)[0]
        low, high = -7, 7
        action_next = (low + (0.5 * (scaled_action + 1.0) * (high - low)))
        # print(action_next.detach().numpy()
        state = perturbed_state.detach().requires_grad_(True)
        # print(f'state:{perturbed_state}')
    # print(f'action:{_action}, action_pertubed:{action_next}, op_action:{op_action}')
        dist = np.linalg.norm(_state - env.center)
        obs_dist = np.linalg.norm(_state - env.obstacle)
        pertub_dist = np.linalg.norm(state.detach().numpy() - env.center)
        pertub_obs_dist = np.linalg.norm(state.detach().numpy() - env.obstacle)
        next_obs_dist =  np.linalg.norm(odeint(bicycle, state.detach()[0], ts, args=(action_next.detach(),))[-1] - env.obstacle)
        if pertub_obs_dist - env.safe_norm_radius > 0:
            
            if next_obs_dist < effect:
                effect = next_obs_dist
                # print(effect)
                attack = (state.detach().numpy() - _state)[0]
    if attack is None:
        return np.zeros_like(_state)
    else:
        # print('find solution')
        return attack
        
    #     if np.minimum(env.target_norm_radius - pertub_dist, pertub_obs_dist - env.safe_norm_radius) >= \
    #         np.minimum(env.target_norm_radius - dist, obs_dist - env.safe_norm_radius):
            
    #         # print(_action)
    #         # print(action.detach())
    #         if next_obs_dist < next_origin_obs_dist:
    #             # print('find solution')
    #             if next_obs_dist < effect:
    #                 effect = next_obs_dist
    #                 # print(effect)
    #                 attack = (state.detach().numpy() - _state)[0]
                  
    # # print('not find solution')
    # if attack is None:
    #     return np.zeros_like(_state)
    # else:
    #     # print('find solution')
    #     return attack

    
# def safe_attack(env, state, model, epsilon, policy, norm, args):
    
#     action = model.predict(state, deterministic=True)[0]
#     _action = action
#     _state = state
#     # state = np.reshape(state, (3,1))
#     def f(x):
#     # Objective function
#         ts = [env.horizon[env.steps], env.horizon[env.steps+1] ]
        
#         return np.linalg.norm(odeint(bicycle, env.state, ts, args=(x,))[-1] - env.obstacle )
#     x_start = np.array(action)
#     lim = [-7, 7]

#     bounds = Bounds([lim[0], lim[0]], [lim[1], lim[1]])  

#     ts = [env.horizon[env.steps], env.horizon[env.steps+1] ]
#     x_state = odeint(bicycle, state, ts, args=(action,))[-1]
#     non_linear_eq= lambda x: env.target_norm_radius - np.linalg.norm(odeint(bicycle, state, ts, args=(x,))[-1] - env.center) +\
#     np.linalg.norm(odeint(bicycle, state, ts, args=(x,))[-1] - env.obstacle) - 0.3-\
#      (env.target_norm_radius - np.linalg.norm(odeint(bicycle, state, ts, args=(action,))[-1] - env.center) +\
#     np.linalg.norm(odeint(bicycle, state, ts, args=(action,))[-1] - env.obstacle) - 0.3)
    
#     dist = np.linalg.norm(x_state - env.center)
#     obs_dist = np.linalg.norm(x_state - env.obstacle)
#     reward = env.target_norm_radius - dist + obs_dist - 0.3
#     non_linear_constr = NonlinearConstraint(non_linear_eq, 0.0, np.inf)
#     # result = minimize(f, x_start, method='trust-constr', bounds=bounds, constraints=non_linear_constr)
#     result = minimize(f, x_start, method='trust-constr', bounds=bounds)
   
#     op_action = (result.x)
    
#     state = torch.from_numpy(state)
    
#     state = state.detach().unsqueeze(0).requires_grad_(True)
#     # print(model.predict(state, deterministic=True)[0])
#     for i in range(100):
     
#         action = model.actor(state, deterministic=True)[0].requires_grad_(True)
#         action = action * 7
#         action = action.double()
#         mse = nn.MSELoss()
        
#         # compute the distance
#         pdist = torch.nn.PairwiseDistance(p=2)
#         loss = pdist(torch.tensor([op_action]), action)
        
#         # loss = mse(torch.tensor([op_action]).requires_grad_(True), action)
#         model.actor.zero_grad()
#         loss = loss.double()
#         # print(action.dtype)
#         loss.backward()
       
#         state_grad = state.grad.detach().squeeze()
#         perturbed_state = state - epsilon / 40 * state_grad.sign()
#         # print(state_grad)
#         # project!
#         # print(perturbed_state[0])
#         torch.clamp(perturbed_state, min=(state - epsilon), max=(state + epsilon))
#         # print(perturbed_state[0])
        
#         scaled_action = model.actor(perturbed_state, deterministic=True)[0]
#         low, high = -7, 7
#         action_next = low + (0.5 * (scaled_action + 1.0) * (high - low))
#         state = perturbed_state.detach().requires_grad_(True)
#         # print(f'state:{perturbed_state}')
#     # print(f'action:{_action}, action_pertubed:{action_next}, op_action:{op_action}')
#     return  state.detach().numpy() - _state


In [ ]:
# Test 50 traces for safe attack

# norm = 2
norm = float('inf')
res_list = []
epsilon = 2
policy = None
args = None
env = bicycleEnv()
model = SAC.load("SAC_bicycle.zip", env=env)
clean_env = bicycleEnv()
state = env.reset()
dims0 = []
dims1 = []
dims2 = []
euclids = []
obs_dists = []
obs_dists_list = []
dist_list = []
center = [1,1,0,math.sqrt(2)]
obstacle = [0.5,0.5,0,math.sqrt(2)/2]
num_reached = 0
action_list = []
pertub_action_list = [] 
number_violate = 0
clean_obs_dists = []
clean_obs_dists_list = []
clean_num_reached = 0
clean_number_violate = 0
clean_obs_dist_list = []
clean_dist_list = []
for j in range(100):
    dim0 = []
    dim1 = []
    dim2 = []
    euclid = []
    state = env.reset()
    _ = clean_env.reset()
    clean_env.state = state
    clean_state = state
    # print(f'state:{state}, clean_state:{clean_state}')
    # Print initial state
    for i in range(env.step_const):
      
        # action = model.predict(state, deterministic=True)
        # pertub_action = safe_attack(env, state, model, epsilon, policy, norm, args)
        attack = safe_attack(env, state, model, epsilon, policy, norm, args)
        # print(attack)
        pertub_state = state + attack
        # print(pertub_state, state)
        pertub_action = model.predict(pertub_state, deterministic=True)[0]
        # print(pertub_action)
        # new_state, reward, done, _ = env.step(pertub_action[0])
        new_state, reward, done, _ = env.step(pertub_action)
        state = new_state
        # new_state, reward, done, _ = env.step(action[0])
        
        dist = np.linalg.norm(state - env.center)
        obs_dist = np.linalg.norm(state - env.obstacle)
        pertub_action_list.append(pertub_action[0])
        # action_list.append(action)
        
        obs_dists.append(obs_dist)
        if obs_dist <= env.safe_norm_radius:
            number_violate += 1
            break
        if dist <= env.target_norm_radius: # stop
            num_reached += 1
            break
        
    # print(obs_dists)
    # print('++++++++++++++++')
    obs_dists_list.append(obs_dists)
    obs_dists = []
    
    # print(env.final_reward_cache)
    # print("dirty env")
    # print(obs_dist_list)
    # print(dist_list)
   
    for i in range(env.step_const):
        clean_action = model.predict(clean_state, deterministic=True)
        clean_new_state, reward, done, _ = clean_env.step(clean_action[0])
        clean_state = clean_new_state
        clean_dist = np.linalg.norm(clean_state - clean_env.center)
        clean_obs_dist = np.linalg.norm(clean_state - clean_env.obstacle)
        # euclid.append(dist)
        
        # clean_obs_dist_list.append(clean_obs_dist)
        clean_dist_list.append(clean_dist)
        clean_obs_dists.append(clean_obs_dist)
        if clean_obs_dist <= env.safe_norm_radius:
            clean_number_violate += 1
            break
        if clean_dist <=  env.target_norm_radius: # stop
            clean_num_reached += 1
            break
    # print(clean_obs_dists)
    # print('-------------------')
    clean_obs_dists_list.append(clean_obs_dists)
    clean_obs_dists = []
    
    # print(clean_env.final_reward_cache)
    # print("clean env")
    # print(clean_obs_dist_list)
    # print(clean_dist_list)
   
    # dims0.append(dim0)
    # dims1.append(dim1)
    # dims2.append(dim2)
    euclids.append(euclid)
ref= [math.pi/2]*30
print("Total number reached = " + str(num_reached))
print("Total number violate = " + str(number_violate))
# print("average of obs dist= " + str(sum(obs_dist_list) / len(obs_dist_list)))
res_list.append(num_reached)
print("clean env for reference")
print("Total number reached = " + str(clean_num_reached))
print("Total number violate = " + str(clean_number_violate))
# print("average of obs dist= " + str(sum(clean_obs_dist_list) / len(clean_obs_dist_list)))

In [ ]:
# print((obs_dists_list[0]))

plt.subplot(1, 2, 1)
ave_dist = []
for i in range(10):
    # ave_dist.append(sum(obs_dists_list[i]) / len(obs_dists_list[i]))
    ave_dist.append(min(obs_dists_list[i]))
    # print(obs_dists_list[i])
    # plt.plot(np.arange(len(obs_dists_list[i])), obs_dists_list[i], color='red')
# print(ave_dist)
plt.boxplot(ave_dist)    
plt.ylim((-1, 8))   
plt.axhline(y=0.3, color='g', linestyle='--')
plt.axhline(y=0, color='g', linestyle='--')
plt.plot()
plt.xlabel('Time steps')
plt.ylabel('distance to unsafe', fontsize = 15)
plt.title('env being attacked')
# plt.show()


plt.subplot(1, 2, 2)
ave_dist = []
for i in range(10):
#         ave_dist.append(sum(clean_obs_dists_list[i]) / len(clean_obs_dists_list[i]))
    ave_dist.append(min(clean_obs_dists_list[i]))
    # plt.plot(np.arange(len(clean_obs_dists_list[i])), clean_obs_dists_list[i], color='green')
# print(ave_dist)
plt.boxplot(ave_dist)    
plt.ylim((-1, 8))       
plt.axhline(y=0.3, color='g', linestyle='--')
plt.axhline(y=0, color='g', linestyle='--')
plt.plot()
plt.xlabel('Time steps')
# plt.ylabel('obstacle distance')
plt.title('clean env')
plt.show()